<h1>CURRENTS Credit Management Model V1</h1>


<h2>Model introduction</h2>

The model simulates a single user who makes random trades within a marketplace using a mutual credit currency. Since users can spend into negative balance, the basis of a good mutual credit design is the appropriate management of credit. The model is designed to help test the appropriateness of various credit management logics.   

### Questions

1. Given varying variables in the credit management logic, how is user behaviour effected?
2. Given different user types, what credit management logic best supports the overall aims of the ecosystem design (i.e. does their balance tend towards 'equilibrium').
3. Does the system accomodate different categories of users? For example, both high & low volume transactors? 

### Assumptions

1. Users who maintain equilibrium are generally rewarded with larger credit access. 
2. For some portion of users, transaction volumes will increase over time as they become key nodes within their respective ecosystems. Consequently, their credit allowance should increase with volume provided they maintain sufficient balance equilibrium over time. 

### Constraints / Scope

* The intention of this model is to generate insights that wil inform the design of the 'Currents' credit management algorithm

# 0. Dependencies

In [297]:
# Standard libraries: https://docs.python.org/3/library/
import math
from numpy import random

# Analysis and plotting modules
import pandas as pd
# import plotly
import plotly.express as px
from random import normalvariate

# cadCAD configuration modules
from cadCAD.configuration.utils import config_sim
from cadCAD.configuration import Experiment

# cadCAD simulation engine modules
from cadCAD.engine import ExecutionContext, Executor


# 1. State Variables & System Parameters

In [298]:
transactionList = []
balanceHistory = [] # a record of the user's running balance'
avgBalanceHistory = []
sendVolHistory = []
time = 1000



# states are defined as python dictionaries:
initial_state = {
    'userBalance' : 0,
    'avgUserBalance' : 0,
    'totalNumTransactions' : 0,
    'userCredit' : 250,
    'userCapacity' : 250,
    'sendVolume' : 0, # volume over X send transactions specified by 'creditCalcVolume' param
    'avgSendVolume': 0, # used to smooth credit allowance
    'transaction' : 0
}


# System parameters:

system_params = {
    'integrity_coefficient': [1], # determines user's balance proclivity (max = 1.0 = balanced spending & receiving)
    'AVG_ammount': [100], # Average transaction ammount
    'creditCalcVolume': [30] # How many previous transactions to use in credit calculation (i.e. 'send volume')
    
}



MONTE_CARLO_RUNS = 10

seeds = [random.RandomState(i) for i in range(MONTE_CARLO_RUNS)] #flexible way to create unique seeds for each monte carlo run


# Policy functions

In [299]:
# Generate random incoming and outgoing User transactions
def p_transact(params, substep, state_history, previous_state):
    
    run = previous_state['run']
    integ = params['integrity_coefficient']
    capacity = previous_state['userCapacity']
    avgTransaction = params['AVG_ammount']
    
    # randomly switch between (-) and (+) transactions, indicating sending or receiving
    posNeg = [-1, 1]
    switch = posNeg[seeds[run-1].randint(0,2)]
    
    # generate random transaction amount
    transaction = avgTransaction * (seeds[run-1].rand()+0.5) 
    
    # randomly switch transaction to incoming/outgoing 
    transaction = transaction * switch
    
    y = seeds[run-1].rand()
    #add some random large transactions to the mix
    if(y > 0.9):
        tLarge = transaction*2*y
        if (tLarge < capacity):
            transaction = tLarge
        
    
    y = seeds[run-1].rand()
    # Generate some large outgoing transactions based on integrity (limited by available capacity)
    if(y > integ):
        tLarge = transaction * 10
        if(tLarge < capacity): # ensure not larger than current spend capacity
            transaction = tLarge * (seeds[run-1].uniform(-1,integ)) # make some outgoing (determined by user integrity)

        
    
    # update total number of transactions
    x = previous_state['totalNumTransactions'] + 1
    
    if(previous_state['totalNumTransactions'] == time):
        transactionList.clear()
        balanceHistory.clear()
        avgBalanceHistory.clear()
        avgSendVolHistory.clear()
    
    return {'transaction_ammount': transaction, 'totalNumTransactions': x}

    
def p_updateUserCapacity(params, substep, state_history, previous_state):
    
    x = previous_state['userBalance'] + previous_state['userCredit']
    return {'newUserCapacity': x}


# Sum X number of outgoing transactions based on 'creditCalcVolume' parameter (informs credit allowance)
def p_calculateSendVolume(params, substep, state_history, previous_state):
    
    x = 0
    posHistory = []
    y = params['creditCalcVolume']
    
    # append only outgoing transactions to new list
    for i in transactionList:
        if(i>0):
            posHistory.append(i)
            
    
    # filter last X transactions (defined by 'creditCalcVolume')
    filteredPosHistory = posHistory[(-1*y):]
    
    for p in filteredPosHistory:
        x = x + p
    
    return {'sendVolume': x}


def p_updateAVGSendVol(params, substep, state_history, previous_state):
    x = 0
    p = previous_state['avgSendVolume']
    
    # sum total
    for i in sendVolHistory:
        x = x + i
    # calculate average
    length = len(sendVolHistory)
    if(length > 0):
        p = x / length
    else:
        p = 0       
    
    return {'avgSendVolume': p}


def p_updateAVGBalance(params, substep, state_history, previous_state):
    
    x = 0
    y = params['creditCalcVolume']
    p = previous_state['avgUserBalance']
    
    filBHist = balanceHistory[(-1*90):]
    # filBHist = balanceHistory # uncomment to calc AVG balance over entire period
    
    # sum total
    for i in filBHist:
        x = x + i   
    
    # calc average
    length = len(filBHist)
    if (length > 0): #ensure no division by zero
        p = x / length
    else:
        p = 0
    
    return {'avgUserBalance': p}



# CREDIT MANAGEMENT LOGIC

def p_updateUserCredit(params, substep, state_history, previous_state):
    
    # fetch appropriate variables
    avgBalance = previous_state['avgUserBalance']
    avgSendVol = previous_state['avgSendVolume']
    x = previous_state['userCredit']
    avgTrans = params['AVG_ammount']
    
    
    # Before we have enough behavioural data, stick with default credit limit
    if (len(transactionList) > 30):
        
        t = 0
        
        if(avgSendVol != 0):
            s = avgBalance/avgSendVol # if balance is low, s will be high
            t = -3*(s**2) + 1 # quadratic (c was = 1)
            t = round(t, 2)
        
        x = t*avgSendVol
            
        # ensure credit allowance doesn't go below zero
        if(x<0):
            x = previous_state['userCredit']
            
        # activate line below to remove Credit Management:
        # x = previous_state['userCredit']
    
    return {'userCredit': x}
    
    

# State Update Functions

In [300]:
# Update current balance based previous transaction
def s_userBalance(params, substep, state_history, previous_state, policy_input):
    
    newBalance = previous_state['userBalance'] + policy_input['transaction_ammount'] 
       
    # keep record of running balance over time (until we know how to access state_history, lol)
    balanceHistory.append(newBalance)
    
    return ('userBalance', newBalance)

# update current average balance (note: distinct from current 'userBalance')
def s_AVGBalance(params, substep, state_history, previous_state, policy_input):
    x = policy_input['avgUserBalance']
    
    # keep record of AVG balance over time (until we know how to access state_history, lol)
    avgBalanceHistory.append(x)
    
    return ('avgUserBalance', x)


def s_totalNumTransactions(params, substep, state_history, previous_state, policy_input):
    x = policy_input['totalNumTransactions']
    return ('totalNumTransactions', x)


def s_userCapacity(params, substep, state_history, previous_state, policy_input):
    x = policy_input['newUserCapacity']
    y = int(round(x))
    return ('userCapacity', y)


def s_userSendVolume(params, substep, state_history, previous_state, policy_input):  
    x = policy_input['sendVolume']
    
    # keep a record
    sendVolHistory.append(x)
    
    return ('sendVolume', x)


def s_avgSendVolume(params, substep, state_history, previous_state, policy_input):
    x = policy_input['avgSendVolume']
    x = int(round(x))
    return ('avgSendVolume', x)
    

def s_userCredit(params, substep, state_history, previous_state, policy_input):
    x =  policy_input['userCredit']
    y = int(round(x))
    return ('userCredit', y)


def s_transaction(params, substep, state_history, previous_state, policy_input):
    
    x = policy_input['transaction_ammount']
    y = int(round(x))
    transactionList.append(y)
    
    return ('transaction', y)



In [301]:
partial_state_update_blocks = [
    {
        'policies': {
            'transact': p_transact,
            'updateUserCapacity': p_updateUserCapacity,
            'calculateSendVolume': p_calculateSendVolume,
            'avgSendVolume': p_updateAVGSendVol,
            'avgUserBalance' : p_updateAVGBalance,
            'updateUserCredit': p_updateUserCredit
        },
        'variables': {
            'userBalance': s_userBalance,
            'avgUserBalance': s_AVGBalance,
            'userCredit': s_userCredit,
            'userCapacity': s_userCapacity,
            'sendVolume': s_userSendVolume,
            'avgSendVolume': s_avgSendVolume,
            'transaction': s_transaction,
            'totalNumTransactions': s_totalNumTransactions
                      
        }
    }
]



In [302]:
from cadCAD import configs
del configs[:] # Clear any prior configs

#reset global variables
transactionList.clear()
balanceHistory.clear()
avgBalanceHistory.clear()
sendVolHistory.clear()

sim_config = config_sim({
    'N': 10,
    'T': range(time),
    'M': system_params
})


experiment = Experiment()
experiment.append_configs(
    initial_state = initial_state,
    partial_state_update_blocks = partial_state_update_blocks,
    sim_configs = sim_config
)



In [303]:
exec_context = ExecutionContext()
run = Executor(exec_context=exec_context, configs=configs)

(system_events, tensor_field, sessions) = run.execute()


                  ___________    ____
  ________ __ ___/ / ____/   |  / __ \
 / ___/ __` / __  / /   / /| | / / / /
/ /__/ /_/ / /_/ / /___/ ___ |/ /_/ /
\___/\__,_/\__,_/\____/_/  |_/_____/
by cadCAD

Execution Mode: local_proc
Configuration Count: 1
Dimensions of the first simulation: (Timesteps, Params, Runs, Vars) = (1000, 3, 10, 8)
Execution Method: local_simulations
SimIDs   : [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
SubsetIDs: [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Ns       : [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
ExpIDs   : [0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Execution Mode: parallelized
Total execution time: 6.32s


In [304]:
simulation_result = pd.DataFrame(system_events)
simulation_result.head(143)

userBalance  avgUserBalance  totalNumTransactions  userCredit  \
0       0.000000        0.000000                     0         250   
1    -109.284462        0.000000                     1         250   
2     -16.918982     -109.284462                     2         250   
3     -72.590280      -63.101722                     3         250   
4      30.299212      -66.264574                     4         250   
..           ...             ...                   ...         ...   
138 -1231.033840      279.924177                   138        2477   
139 -1111.426123      256.658381                   139        2480   
140  -841.336718      233.332672                   140        2508   
141  -906.184527      212.230181                   141        2537   
142 -1011.392355      187.523246                   142        2541   

     userCapacity  sendVolume  avgSendVolume  transaction  simulation  subset  \
0             250           0              0            0           0       0   
1             250           0              0         -109           0       0   
2             141           0              0           92           0       0   
3             233          92              0          -56           0       0   
4             177          92             31          103           0       0   
..            ...         ...            ...          ...         ...     ...   
138          1273        3025           2583          -57           0       0   
139          1246        3025           2586          120           0       0   
140          1369        3041           2589          270           0       0   
141          1667        3214           2593          -65           0       0   
142          1631        3214           2597         -105           0       0   

     run  substep  timestep  
0      1        0         0  
1      1        1         1  
2      1        1         2  
3      1        1         3  
4      1        1         4  
..   ...      ...       ...  
138    1        1       138  
139    1        1       139  
140    1        1       140  
141    1        1       141  
142    1        1       142  

[143 rows x 13 columns]

### 8. Simulation Output Preparation

In [305]:
# Get system events and attribute index
df = (pd.DataFrame(system_events)
        .assign(days=lambda df: df.timestep)
        .query('timestep > 1')
        .query('timestep < 1000')
     )

# Clean substeps
first_ind = (df.substep == 0) & (df.timestep == 0)
last_ind = df.substep == max(df.substep)
inds_to_drop = (first_ind | last_ind)
df = df.loc[inds_to_drop].drop(columns=['substep'])

# Attribute parameters to each row
df = df.assign(**configs[0].sim_config['M'])
for i, (_, n_df) in enumerate(df.groupby(['simulation', 'subset', 'run'])):
    df.loc[n_df.index] = n_df.assign(**configs[i].sim_config['M'])
    

In [306]:
pd.options.plotting.backend = "plotly"

# plot something else by querying the dataframe
fig_df = df.query('run == 1')
# fig_df = df

fig_df.plot(
    kind='line',
    x='timestep',
    y=['avgUserBalance', 'userCredit', 'transaction', 'avgSendVolume', 'userCapacity']
)

In [307]:
fig = px.line(
    df,
    x='timestep',
    y=['avgUserBalance', 'userCredit', 'sendVolume'],
    facet_row='simulation',
    facet_col='run',
    height=400,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=30, r=20, t=20, b=20),
)

fig.show()

In [308]:
# fig_df = df.query()
fig_df = df

fig = px.scatter(
    fig_df,
    x=fig_df.days,
    y=fig_df.userBalance,
    color=fig_df.integrity_coefficient.astype(str),
    opacity=0.1,
    trendline="lowess",
    labels={'color': 'integrity_coefficient'}
)

fig.show()

In [309]:
fig3 = px.scatter(
    df[df.timestep >= 0],
    x='avgUserBalance',
    y='userCredit',
    color='timestep'
)
fig3.show()